In [1]:
import pandas as pd
import numpy as np
from sklearn.datasets import make_classification
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.svm import SVR, LinearSVR, SVC, LinearSVC
from sklearn.metrics import accuracy_score, mean_squared_error, mean_absolute_error
from time import time
import matplotlib.pyplot as plt
import copy
from tqdm import tqdm

In [2]:
from rkhs.rff import RFF
from rkhs.nystrom import PlainNystromRegressor, SGDPlainNystromRegressor, SGDPlainNystromClassifier, FALKON

# CT

In [3]:
data = pd.read_csv('data/slice_localization_data.zip')

In [4]:
features = data.drop('reference', axis=1)
y = data.loc[:,'reference']
X_train, X_test, y_train, y_test = train_test_split(features, y, random_state=24)
X_train = X_train.values
X_test = X_test.values

In [5]:
nD = 10
list_D = np.linspace(300,3500,nD,dtype=int)
nb_iter = 5

In [6]:
mse_falkon = np.empty((nD,nb_iter))
mse_train_falkon = np.empty((nD,nb_iter))
mae_falkon = np.empty((nD,nb_iter))
mae_train_falkon = np.empty((nD,nb_iter))
times_falkon = np.empty((nD,nb_iter))

for i,D in enumerate(tqdm(list_D)):
    for j in range(nb_iter):
        falkon = Pipeline([('Scaler',StandardScaler()),
                           ('FALKON', FALKON(m=D)),])
        
        t0 = time()
        falkon.fit(X_train, y_train)
        times_falkon[i,j] = time() - t0
        
        y_pred_train_falkon = falkon.predict(X_train)                      
        mse_train_falkon[i,j] = mean_squared_error(y_train, y_pred_train_falkon)
        mae_train_falkon[i,j] = mean_absolute_error(y_train, y_pred_train_falkon)
        
        y_pred_falkon = falkon.predict(X_test)                      
        mse_falkon[i,j] = mean_squared_error(y_test, y_pred_falkon)
        mae_falkon[i,j] = mean_absolute_error(y_test, y_pred_falkon)

 56%|█████▌    | 56/100 [00:15<00:11,  3.76it/s, improvement=6.39e-6]


 67%|██████▋   | 67/100 [00:17<00:08,  3.87it/s, improvement=1.48e-9]

  0%|          | 0/100 [00:00<?, ?it/s]

  0%|          | 0/100 [00:00<?, ?it/s, improvement=0.00416]

  1%|          | 1/100 [00:00<00:24,  4.08it/s, improvement=0.00416]

  1%|          | 1/100 [00:00<00:24,  4.08it/s, improvement=0.0198] 

  2%|▏         | 2/100 [00:00<00:24,  4.02it/s, improvement=0.0198]

  2%|▏         | 2/100 [00:00<00:24,  4.02it/s, improvement=0.00454]

  3%|▎         | 3/100 [00:00<00:24,  4.00it/s, improvement=0.00454]

  3%|▎         | 3/100 [00:01<00:24,  4.00it/s, improvement=0.18]   

  4%|▍         | 4/100 [00:01<00:24,  4.00it/s, improvement=0.18]

  4%|▍         | 4/100 [00:01<00:24,  4.00it/s, improvement=0.0696]

  5%|▌         | 5/100 [00:01<00:23,  3.99it/s, improvement=0.0696]

  5%|▌         | 5/100 [00:01<00:23,  3.99it/s, improvement=0.191] 

  6%|▌         | 6/100 [00:01<00:23,  4.01it/s, improvement=0.191]

  6%|▌         | 6/100 [00:01<00:23,  4.01it/s, improvement=3.33e

  1%|          | 1/100 [00:00<00:24,  4.01it/s, improvement=0.0488]


  2%|▏         | 2/100 [00:00<00:24,  4.01it/s, improvement=0.0488]


  2%|▏         | 2/100 [00:00<00:24,  4.01it/s, improvement=0.0252]


  3%|▎         | 3/100 [00:00<00:24,  3.96it/s, improvement=0.0252]


  3%|▎         | 3/100 [00:01<00:24,  3.96it/s, improvement=0.118] 


  4%|▍         | 4/100 [00:01<00:24,  3.94it/s, improvement=0.118]


  4%|▍         | 4/100 [00:01<00:24,  3.94it/s, improvement=0.0783]


  5%|▌         | 5/100 [00:01<00:24,  3.91it/s, improvement=0.0783]


  5%|▌         | 5/100 [00:01<00:24,  3.91it/s, improvement=0.137] 


  6%|▌         | 6/100 [00:01<00:23,  3.93it/s, improvement=0.137]


  6%|▌         | 6/100 [00:01<00:23,  3.93it/s, improvement=0.0125]


  7%|▋         | 7/100 [00:01<00:23,  3.95it/s, improvement=0.0125]


  7%|▋         | 7/100 [00:02<00:23,  3.95it/s, improvement=0.122] 


  8%|▊         | 8/100 [00:02<00:23,  3.96it/s, improvement=0.122]


  8%|▊         | 8/100 

 52%|█████▏    | 52/100 [00:13<00:12,  3.89it/s, improvement=0.0963]


 53%|█████▎    | 53/100 [00:13<00:12,  3.87it/s, improvement=0.0963]


 53%|█████▎    | 53/100 [00:13<00:12,  3.87it/s, improvement=0.0319]


 54%|█████▍    | 54/100 [00:13<00:12,  3.79it/s, improvement=0.0319]


 54%|█████▍    | 54/100 [00:14<00:12,  3.79it/s, improvement=0.0828]


 55%|█████▌    | 55/100 [00:14<00:11,  3.81it/s, improvement=0.0828]


 55%|█████▌    | 55/100 [00:14<00:11,  3.81it/s, improvement=0.722] 


 56%|█████▌    | 56/100 [00:14<00:11,  3.80it/s, improvement=0.722]


 56%|█████▌    | 56/100 [00:14<00:11,  3.80it/s, improvement=5.94e-7]


 57%|█████▋    | 57/100 [00:14<00:11,  3.82it/s, improvement=5.94e-7]


 57%|█████▋    | 57/100 [00:14<00:11,  3.82it/s, improvement=0.00147]


 58%|█████▊    | 58/100 [00:14<00:10,  3.86it/s, improvement=0.00147]


 58%|█████▊    | 58/100 [00:15<00:10,  3.86it/s, improvement=0.338]  


 59%|█████▉    | 59/100 [00:15<00:10,  3.84it/s, improvement=0.338]


 59

 34%|███▍      | 34/100 [00:08<00:16,  3.89it/s, improvement=0.0496]



 34%|███▍      | 34/100 [00:09<00:16,  3.89it/s, improvement=0.872] 



 35%|███▌      | 35/100 [00:09<00:16,  3.87it/s, improvement=0.872]



 35%|███▌      | 35/100 [00:09<00:16,  3.87it/s, improvement=0.0606]



 36%|███▌      | 36/100 [00:09<00:16,  3.87it/s, improvement=0.0606]



 36%|███▌      | 36/100 [00:09<00:16,  3.87it/s, improvement=0.527] 



 37%|███▋      | 37/100 [00:09<00:16,  3.84it/s, improvement=0.527]



 37%|███▋      | 37/100 [00:09<00:16,  3.84it/s, improvement=0.0288]



 38%|███▊      | 38/100 [00:09<00:16,  3.85it/s, improvement=0.0288]



 38%|███▊      | 38/100 [00:10<00:16,  3.85it/s, improvement=2.67]  



 39%|███▉      | 39/100 [00:10<00:15,  3.88it/s, improvement=2.67]



 39%|███▉      | 39/100 [00:10<00:15,  3.88it/s, improvement=0.07]



 40%|████      | 40/100 [00:10<00:15,  3.92it/s, improvement=0.07]



 40%|████      | 40/100 [00:10<00:15,  3.92it/s, improvement=1.36]



 4

...

  5%|▌         | 5/100 [00:10<03:22,  2.13s/it, improvement=6.24e-6]



































  5%|▌         | 5/100 [00:12<03:22,  2.13s/it, improvement=1.01e-5]



































  6%|▌         | 6/100 [00:12<03:19,  2.12s/it, improvement=1.01e-5]



































  6%|▌         | 6/100 [00:14<03:19,  2.12s/it, improvement=1.11e-10]




































  0%|          | 0/100 [00:00<?, ?it/s]




































  0%|          | 0/100 [00:02<?, ?it/s, improvement=1.38e-6]




































  1%|          | 1/100 [00:02<03:33,  2.15s/it, improvement=1.38e-6]




































  1%|          | 1/100 [00:04<03:33,  2.15s/it, improvement=9.71e-7]




































  2%|▏         | 2/100 [00:04<03:30,  2.15s/it, improvement=9.71e-7]




































  2%|▏         | 2/100 [00:06<03:30,  2.15s/it, improvement=7.18e-6]



























  4%|▍         | 4/100 [00:10<04:07,  2.58s/it, improvement=2.99e-6]





































  4%|▍         | 4/100 [00:12<04:07,  2.58s/it, improvement=3.3e-6] 





































  5%|▌         | 5/100 [00:12<04:05,  2.58s/it, improvement=3.3e-6]





































  5%|▌         | 5/100 [00:15<04:05,  2.58s/it, improvement=4e-6]  





































  6%|▌         | 6/100 [00:15<04:01,  2.57s/it, improvement=4e-6]





































  6%|▌         | 6/100 [00:18<04:01,  2.57s/it, improvement=2.28e-9]






































  0%|          | 0/100 [00:00<?, ?it/s]






































  0%|          | 0/100 [00:02<?, ?it/s, improvement=9.42e-7]






































  1%|          | 1/100 [00:02<04:13,  2.56s/it, improvement=9.42e-7]






































  1%|          | 1/100 [00:05<04:13,  2.56s/it, improvement=5.93e-6]

















 15%|█▌        | 15/100 [00:38<03:37,  2.56s/it, improvement=1.18e-5]






































 15%|█▌        | 15/100 [00:41<03:37,  2.56s/it, improvement=1.01e-6]






































 16%|█▌        | 16/100 [00:41<03:35,  2.56s/it, improvement=1.01e-6]






































 16%|█▌        | 16/100 [00:43<03:35,  2.56s/it, improvement=1.29e-5]






































 17%|█▋        | 17/100 [00:43<03:33,  2.57s/it, improvement=1.29e-5]






































 17%|█▋        | 17/100 [00:46<03:33,  2.57s/it, improvement=9.99e-8]






































 18%|█▊        | 18/100 [00:46<03:32,  2.59s/it, improvement=9.99e-8]






































 18%|█▊        | 18/100 [00:48<03:32,  2.59s/it, improvement=7.16e-5]






































 19%|█▉        | 19/100 [00:48<03:29,  2.59s/it, improvement=7.16e-5]






































 19%|█▉        | 19/100 [00:

  3%|▎         | 3/100 [00:09<05:06,  3.16s/it, improvement=1.69e-6]









































  3%|▎         | 3/100 [00:12<05:06,  3.16s/it, improvement=2.83e-6]









































  4%|▍         | 4/100 [00:12<05:01,  3.14s/it, improvement=2.83e-6]









































  4%|▍         | 4/100 [00:15<05:01,  3.14s/it, improvement=3.58e-6]









































  5%|▌         | 5/100 [00:15<04:58,  3.14s/it, improvement=3.58e-6]









































  5%|▌         | 5/100 [00:18<04:58,  3.14s/it, improvement=1.12e-5]









































  6%|▌         | 6/100 [00:18<04:56,  3.16s/it, improvement=1.12e-5]









































  6%|▌         | 6/100 [00:21<04:56,  3.16s/it, improvement=2.31e-7]









































  7%|▋         | 7/100 [00:21<04:51,  3.13s/it, improvement=2.31e-7]









































  7%|▋    

  0%|          | 0/100 [00:00<?, ?it/s]











































  0%|          | 0/100 [00:03<?, ?it/s, improvement=1.78e-7]











































  1%|          | 1/100 [00:03<05:11,  3.15s/it, improvement=1.78e-7]











































  1%|          | 1/100 [00:06<05:11,  3.15s/it, improvement=5.13e-7]











































  2%|▏         | 2/100 [00:06<05:07,  3.14s/it, improvement=5.13e-7]











































  2%|▏         | 2/100 [00:09<05:07,  3.14s/it, improvement=7.75e-7]











































  3%|▎         | 3/100 [00:09<05:11,  3.21s/it, improvement=7.75e-7]











































  3%|▎         | 3/100 [00:12<05:11,  3.21s/it, improvement=7.68e-6]











































  4%|▍         | 4/100 [00:12<05:04,  3.18s/it, improvement=7.68e-6]











































  4%|▍         | 4/100 [00:15

In [13]:
np.savetxt('CT_results/mse_falkon.csv', mse_falkon, delimiter=',')
np.savetxt('CT_results/mse_train_falkon.csv', mse_train_falkon, delimiter=',')
np.savetxt('CT_results/mae_falkon.csv', mae_falkon, delimiter=',')
np.savetxt('CT_results/mae_train_falkon.csv', mae_train_falkon, delimiter=',')
np.savetxt('CT_results/times_falkon.csv', times_falkon, delimiter=',')

In [15]:
eC_min = -6
eC_max = 1
list_C = [10**i for i in range(eC_min, eC_max+1)]
nC = eC_max-eC_min+1
np.savetxt('CT_results/list_C.csv', list_C, delimiter=',')

In [16]:
mse_falkon_reg = np.empty((nC,nb_iter))
mse_train_falkon_reg = np.empty((nC,nb_iter))
mae_falkon_reg = np.empty((nC,nb_iter))
mae_train_falkon_reg = np.empty((nC,nb_iter))
times_falkon_reg = np.empty((nC,nb_iter))

for i,C in enumerate(tqdm(list_C)):
    for j in range(nb_iter):
        falkon = Pipeline([('Scaler',StandardScaler()),
                           ('FALKON', FALKON(m=300, lambda_reg=C)),])

        t0 = time()
        falkon.fit(X_train, y_train)
        times_falkon_reg[i,j] = time() - t0
        
        y_pred_train_falkon = falkon.predict(X_train)                      
        mse_train_falkon_reg[i,j] = mean_squared_error(y_train, y_pred_train_falkon)
        mae_train_falkon_reg[i,j] = mean_absolute_error(y_train, y_pred_train_falkon)
        
        y_pred_falkon = falkon.predict(X_test)                      
        mse_falkon_reg[i,j] = mean_squared_error(y_test, y_pred_falkon)
        mae_falkon_reg[i,j] = mean_absolute_error(y_test, y_pred_falkon)














































  0%|          | 0/8 [00:00<?, ?it/s]













































  0%|          | 0/100 [00:00<?, ?it/s]













































  0%|          | 0/100 [00:00<?, ?it/s, improvement=0.00773]













































  1%|          | 1/100 [00:00<00:25,  3.90it/s, improvement=0.00773]













































  1%|          | 1/100 [00:00<00:25,  3.90it/s, improvement=0.00391]













































  2%|▏         | 2/100 [00:00<00:25,  3.89it/s, improvement=0.00391]













































  2%|▏         | 2/100 [00:00<00:25,  3.89it/s, improvement=0.0121] 













































  3%|▎         | 3/100 [00:00<00:24,  3.93it/s, improvement=0.0121]













































  3%|▎         | 3/100 [00:01<00:24,  3.93it/s, improvement=0.0291]














































 15%|█▌        | 15/100 [00:04<00:24,  3.53it/s, improvement=0.00122]













































 16%|█▌        | 16/100 [00:04<00:23,  3.51it/s, improvement=0.00122]













































 16%|█▌        | 16/100 [00:04<00:23,  3.51it/s, improvement=3.23]   













































 17%|█▋        | 17/100 [00:04<00:23,  3.52it/s, improvement=3.23]













































 17%|█▋        | 17/100 [00:04<00:23,  3.52it/s, improvement=7.85e-7]













































 18%|█▊        | 18/100 [00:04<00:23,  3.53it/s, improvement=7.85e-7]













































 18%|█▊        | 18/100 [00:05<00:23,  3.53it/s, improvement=1.77]   













































 19%|█▉        | 19/100 [00:05<00:23,  3.52it/s, improvement=1.77]













































 19%|█▉        | 19/100 [00:05<00:23,  3.52it/s, improvement=0.0518]



















 31%|███       | 31/100 [00:08<00:17,  4.02it/s, improvement=0.0188]













































 32%|███▏      | 32/100 [00:08<00:17,  3.96it/s, improvement=0.0188]













































 32%|███▏      | 32/100 [00:08<00:17,  3.96it/s, improvement=1.24]  













































 33%|███▎      | 33/100 [00:08<00:17,  3.89it/s, improvement=1.24]













































 33%|███▎      | 33/100 [00:08<00:17,  3.89it/s, improvement=8.96e-5]













































 34%|███▍      | 34/100 [00:08<00:16,  3.92it/s, improvement=8.96e-5]













































 34%|███▍      | 34/100 [00:08<00:16,  3.92it/s, improvement=0.183]  













































 35%|███▌      | 35/100 [00:08<00:16,  3.95it/s, improvement=0.183]













































 35%|███▌      | 35/100 [00:09<00:16,  3.95it/s, improvement=0.319]






















 47%|████▋     | 47/100 [00:12<00:14,  3.78it/s, improvement=0.309]  













































 48%|████▊     | 48/100 [00:12<00:13,  3.72it/s, improvement=0.309]













































 48%|████▊     | 48/100 [00:12<00:13,  3.72it/s, improvement=5.56e-7]













































 49%|████▉     | 49/100 [00:12<00:13,  3.66it/s, improvement=5.56e-7]













































 49%|████▉     | 49/100 [00:12<00:13,  3.66it/s, improvement=0.487]  













































 50%|█████     | 50/100 [00:12<00:13,  3.70it/s, improvement=0.487]













































 50%|█████     | 50/100 [00:13<00:13,  3.70it/s, improvement=0.000263]













































 51%|█████     | 51/100 [00:13<00:13,  3.73it/s, improvement=0.000263]













































 51%|█████     | 51/100 [00:13<00:13,  3.73it/s, improvement=0.811]   













 63%|██████▎   | 63/100 [00:16<00:09,  3.90it/s, improvement=1.79e-6]













































 64%|██████▍   | 64/100 [00:16<00:09,  3.90it/s, improvement=1.79e-6]













































 64%|██████▍   | 64/100 [00:16<00:09,  3.90it/s, improvement=5.4e-6] 













































 65%|██████▌   | 65/100 [00:16<00:08,  3.90it/s, improvement=5.4e-6]













































 65%|██████▌   | 65/100 [00:17<00:08,  3.90it/s, improvement=0.382] 













































 66%|██████▌   | 66/100 [00:17<00:08,  3.89it/s, improvement=0.382]













































 66%|██████▌   | 66/100 [00:17<00:08,  3.89it/s, improvement=0.000607]













































 67%|██████▋   | 67/100 [00:17<00:08,  3.84it/s, improvement=0.000607]













































 67%|██████▋   | 67/100 [00:17<00:08,  3.84it/s, improvement=0.896]   













...

  7%|▋         | 7/100 [00:01<00:25,  3.60it/s, improvement=2.68e-8]
































































  7%|▋         | 7/100 [00:02<00:29,  3.14it/s, improvement=1.44e-11]

































































  0%|          | 0/100 [00:00<?, ?it/s]
































































  0%|          | 0/100 [00:00<?, ?it/s, improvement=32.8]
































































  1%|          | 1/100 [00:00<00:24,  4.00it/s, improvement=32.8]
































































  1%|          | 1/100 [00:00<00:24,  4.00it/s, improvement=11.1]
































































  2%|▏         | 2/100 [00:00<00:24,  3.99it/s, improvement=11.1]
































































  2%|▏         | 2/100 [00:00<00:24,  3.99it/s, improvement=7.49]




















































  3%|▎         | 3/100 [00:01<00:24,  3.90it/s, improvement=0.154]
































































  4%|▍         | 4/100 [00:01<00:24,  3.92it/s, improvement=0.154]
































































  4%|▍         | 4/100 [00:01<00:24,  3.92it/s, improvement=0.00308]
































































  5%|▌         | 5/100 [00:01<00:24,  3.90it/s, improvement=0.00308]
































































  5%|▌         | 5/100 [00:01<00:24,  3.90it/s, improvement=3.29e-5]
































































  6%|▌         | 6/100 [00:01<00:24,  3.91it/s, improvement=3.29e-5]
































































  6%|▌         | 6/100 [00:01<00:24,  3.91it/s, improvement=4.6e-7] 
































































  7%|▋         | 7/100 [00:01<00:23,  3.89it/s, improvement=4.6e-7]







  8%|▊         | 8/100 [00:02<00:24,  3.78it/s, improvement=8.52e-7]

































































  8%|▊         | 8/100 [00:02<00:24,  3.78it/s, improvement=1.64e-8]

































































  9%|▉         | 9/100 [00:02<00:23,  3.80it/s, improvement=1.64e-8]

































































  9%|▉         | 9/100 [00:02<00:26,  3.38it/s, improvement=2.75e-10]













































 88%|████████▊ | 7/8 [08:22<00:50, 50.82s/it]

































































  0%|          | 0/100 [00:00<?, ?it/s]

































































  0%|          | 0/100 [00:00<?, ?it/s, improvement=335]

































































  1%|          | 1/100 [00:00<00:24,  4.00it/s, improvement=335]

































































  1%|          

  0%|          | 0/100 [00:00<?, ?it/s]

































































  0%|          | 0/100 [00:00<?, ?it/s, improvement=325]

































































  1%|          | 1/100 [00:00<00:25,  3.94it/s, improvement=325]

































































  1%|          | 1/100 [00:00<00:25,  3.94it/s, improvement=5.16]

































































  2%|▏         | 2/100 [00:00<00:24,  3.93it/s, improvement=5.16]

































































  2%|▏         | 2/100 [00:00<00:24,  3.93it/s, improvement=0.037]

































































  3%|▎         | 3/100 [00:00<00:24,  3.90it/s, improvement=0.037]

































































  3%|▎         | 3/100 [00:01<00:24,  3.90it/s, improvement=5.26e-5]


















































  2%|▏         | 2/100 [00:00<00:24,  4.00it/s, improvement=0.0146]

































































  3%|▎         | 3/100 [00:00<00:24,  3.94it/s, improvement=0.0146]

































































  3%|▎         | 3/100 [00:01<00:24,  3.94it/s, improvement=2.64e-5]

































































  4%|▍         | 4/100 [00:01<00:24,  3.91it/s, improvement=2.64e-5]

































































  4%|▍         | 4/100 [00:01<00:31,  3.10it/s, improvement=2.18e-9]













































100%|██████████| 8/8 [08:34<00:00, 39.07s/it]




















































































































































































































































































































In [20]:
np.savetxt('CT_results/mse_falkon_reg.csv', mse_falkon_reg, delimiter=',')
np.savetxt('CT_results/mse_train_falkon_reg.csv', mse_train_falkon_reg, delimiter=',')
np.savetxt('CT_results/mae_falkon_reg.csv', mae_falkon_reg, delimiter=',')
np.savetxt('CT_results/mae_train_falkon_reg.csv', mae_train_falkon_reg, delimiter=',')
np.savetxt('CT_results/times_falkon_reg.csv', times_falkon_reg, delimiter=',')

In [21]:
mse_rff_l1 = np.empty((nC,nb_iter))
mse_train_rff_l1 = np.empty((nC,nb_iter))
mae_rff_l1 = np.empty((nC,nb_iter))
mae_train_rff_l1 = np.empty((nC,nb_iter))
times_rff_l1 = np.empty((nC,nb_iter))

for i,C in enumerate(tqdm(list_C)):
    for j in range(nb_iter):
        rff = Pipeline([('Scaler',StandardScaler()),
                        ('RFF',RFF(D = 2000)),
                        ('LinearSVR', LinearSVR(C = C, max_iter=10000)),])
        
        t0 = time()
        rff.fit(X_train, y_train)
        times_rff_l1[i,j] = time() - t0
        
        y_pred_train_rff = rff.predict(X_train)                      
        mse_train_rff_l1[i,j] = mean_squared_error(y_train, y_pred_train_rff)
        mae_train_rff_l1[i,j] = mean_absolute_error(y_train, y_pred_train_rff)
        
        y_pred_rff = rff.predict(X_test)                      
        mse_rff_l1[i,j] = mean_squared_error(y_test, y_pred_rff)
        mae_rff_l1[i,j] = mean_absolute_error(y_test, y_pred_rff)


































































  0%|          | 0/8 [00:00<?, ?it/s]
































































 12%|█▎        | 1/8 [00:58<06:50, 58.64s/it]
































































 25%|██▌       | 2/8 [01:54<05:47, 57.91s/it]
































































 38%|███▊      | 3/8 [02:49<04:44, 56.91s/it]
































































 50%|█████     | 4/8 [03:45<03:46, 56.63s/it]
































































 62%|██████▎   | 5/8 [04:40<02:48, 56.12s/it]
































































 75%|███████▌  | 6/8 [05:40<01:54, 57.42s/it]
































































 88%|████████▊ | 7/8 [07:09<01:06, 66.87s/it]
































































100%|██████████| 8/8 [11:01<00:00, 82.74s/it] 


In [22]:
np.savetxt('CT_results/mse_rff_l1_reg.csv', mse_rff_l1, delimiter=',')
np.savetxt('CT_results/mse_train_rff_l1_reg.csv', mse_train_rff_l1, delimiter=',')
np.savetxt('CT_results/mae_rff_l1_reg.csv', mae_rff_l1, delimiter=',')
np.savetxt('CT_results/mae_train_rff_l1_reg.csv', mae_train_rff_l1, delimiter=',')
np.savetxt('CT_results/times_rff_l1_reg.csv', times_rff_l1, delimiter=',')

In [ ]:
mse_rff_l2 = np.empty((nC,nb_iter))
mse_train_rff_l2 = np.empty((nC,nb_iter))
mae_rff_l2 = np.empty((nC,nb_iter))
mae_train_rff_l2 = np.empty((nC,nb_iter))
times_rff_l2 = np.empty((nC,nb_iter))

for i,C in enumerate(tqdm(list_C)):
    for j in range(nb_iter):
        rff = Pipeline([('Scaler',StandardScaler()),
                        ('RFF',RFF(D = 2000)),
                        ('LinearSVR', LinearSVR(C = C, loss='squared_epsilon_insensitive', max_iter=10000)),])
        
        t0 = time()
        rff.fit(X_train, y_train)
        times_rff_l2[i,j] = time() - t0
        
        y_pred_train_rff = rff.predict(X_train)                      
        mse_train_rff_l2[i,j] = mean_squared_error(y_train, y_pred_train_rff)
        mae_train_rff_l2[i,j] = mean_absolute_error(y_train, y_pred_train_rff)
        
        y_pred_rff = rff.predict(X_test)                      
        mse_rff_l2[i,j] = mean_squared_error(y_test, y_pred_rff)
        mae_rff_l2[i,j] = mean_absolute_error(y_test, y_pred_rff)


































































  0%|          | 0/8 [00:00<?, ?it/s]
































































 12%|█▎        | 1/8 [01:04<07:32, 64.64s/it]
































































 25%|██▌       | 2/8 [02:14<06:37, 66.27s/it]
































































 38%|███▊      | 3/8 [03:19<05:28, 65.75s/it]
































































 50%|█████     | 4/8 [04:26<04:24, 66.12s/it]

In [ ]:
np.savetxt('CT_results/mse_rff_l2_reg.csv', mse_rff_l2, delimiter=',')
np.savetxt('CT_results/mse_train_rff_l2_reg.csv', mse_train_rff_l2, delimiter=',')
np.savetxt('CT_results/mae_rff_l2_reg.csv', mae_rff_l2, delimiter=',')
np.savetxt('CT_results/mae_train_rff_l2_reg.csv', mae_train_rff_l2, delimiter=',')
np.savetxt('CT_results/times_rff_l2_reg.csv', times_rff_l2, delimiter=',')

In [ ]:
mse_nys_plain_reg = np.empty((nC,nb_iter))
mse_train_nys_plain_reg = np.empty((nC,nb_iter))
mae_nys_plain_reg = np.empty((nC,nb_iter))
mae_train_nys_plain_reg = np.empty((nC,nb_iter))
times_nys_plain_reg = np.empty((nC,nb_iter))

for i,C in enumerate(tqdm(list_C)):
    for j in range(nb_iter):
        nys = Pipeline([('Scaler',StandardScaler()),
                        ('nys', PlainNystromRegressor(m=3500, lambda_reg=C)),])
        
        t0 = time()
        nys.fit(X_train, y_train)
        times_nys_plain_reg[i,j] = time() - t0
        
        y_pred_train_nys = nys.predict(X_train)                      
        mse_train_nys_plain_reg[i,j] = mean_squared_error(y_train, y_pred_train_nys)
        mae_train_nys_plain_reg[i,j] = mean_absolute_error(y_train, y_pred_train_nys)
        
        y_pred_nys = nys.predict(X_test)                      
        mse_nys_plain_reg[i,j] = mean_squared_error(y_test, y_pred_nys)
        mae_nys_plain_reg[i,j] = mean_absolute_error(y_test, y_pred_nys)

In [ ]:
np.savetxt('CT_results/mse_nys_plain_reg.csv', mse_nys_plain_reg, delimiter=',')
np.savetxt('CT_results/mse_train_nys_plain_reg.csv', mse_train_nys_plain_reg, delimiter=',')
np.savetxt('CT_results/mae_nys_plain_reg.csv', mae_nys_plain_reg, delimiter=',')
np.savetxt('CT_results/mae_train_nys_plain_reg.csv', mae_train_nys_plain_reg, delimiter=',')
np.savetxt('CT_results/times_nys_plain_reg.csv', times_nys_plain_reg, delimiter=',')

In [ ]:
try:
    mse_nys_l2 = np.empty((nD,nb_iter))
    mse_train_nys_l2 = np.empty((nD,nb_iter))
    mae_nys_l2 = np.empty((nD,nb_iter))
    mae_train_nys_l2 = np.empty((nD,nb_iter))
    times_nys_l2 = np.empty((nD,nb_iter))

    for i,D in enumerate(tqdm(list_D)):
        for j in range(nb_iter):
            nys = Pipeline([('Scaler',StandardScaler()),
                            ('nys', SGDPlainNystromRegressor(m=D)),])

            t0 = time()
            nys.fit(X_train, y_train)
            times_nys_l2[i,j] = time() - t0

            y_pred_train_nys = nys.predict(X_train)                      
            mse_train_nys_l2[i,j] = mean_squared_error(y_train, y_pred_train_nys)
            mae_train_nys_l2[i,j] = mean_absolute_error(y_train, y_pred_train_nys)

            y_pred_nys = nys.predict(X_test)                      
            mse_nys_l2[i,j] = mean_squared_error(y_test, y_pred_nys)
            mae_nys_l2[i,j] = mean_absolute_error(y_test, y_pred_nys)
except:
    pass

In [ ]:
try:
    np.savetxt('CT_results/mse_nys_l2.csv', mse_nys_l2, delimiter=',')
    np.savetxt('CT_results/mse_train_nys_l2.csv', mse_train_nys_l2, delimiter=',')
    np.savetxt('CT_results/mae_nys_l2.csv', mae_nys_l2, delimiter=',')
    np.savetxt('CT_results/mae_train_nys_l2.csv', mae_train_nys_l2, delimiter=',')
    np.savetxt('CT_results/times_nys_l2.csv', times_nys_l2, delimiter=',')
except:
    pass

In [ ]:
try:
    mse_nys_l2_reg_l2 = np.empty((nC,nb_iter))
    mse_train_nys_l2_reg_l2 = np.empty((nC,nb_iter))
    mae_nys_l2_reg_l2 = np.empty((nC,nb_iter))
    mae_train_nys_l2_reg_l2 = np.empty((nC,nb_iter))
    times_nys_l2_reg_l2 = np.empty((nC,nb_iter))

    for i,C in enumerate(tqdm(list_C)):
        for j in range(nb_iter):
            nys = Pipeline([('Scaler',StandardScaler()),
                            ('nys', SGDPlainNystromRegressor(m=1000, lambda_reg=C)),])

            t0 = time()
            nys.fit(X_train, y_train)
            times_nys_l2_reg_l2[i,j] = time() - t0

            y_pred_train_nys = nys.predict(X_train)                      
            mse_train_nys_l2_reg_l2[i,j] = mean_squared_error(y_train, y_pred_train_nys)
            mae_train_nys_l2_reg_l2[i,j] = mean_absolute_error(y_train, y_pred_train_nys)

            y_pred_nys = nys.predict(X_test)                      
            mse_nys_l2_reg_l2[i,j] = mean_squared_error(y_test, y_pred_nys)
            mae_nys_l2_reg_l2[i,j] = mean_absolute_error(y_test, y_pred_nys)
except:
    pass

In [ ]:
try:
    np.savetxt('CT_results/mse_nys_l2_reg_l2.csv', mse_nys_l2_reg_l2, delimiter=',')
    np.savetxt('CT_results/mse_train_nys_l2_reg_l2.csv', mse_train_nys_l2_reg_l2, delimiter=',')
    np.savetxt('CT_results/mae_nys_l2_reg_l2.csv', mae_nys_l2_reg_l2, delimiter=',')
    np.savetxt('CT_results/mae_train_nys_l2_reg_l2.csv', mae_train_nys_l2_reg_l2, delimiter=',')
    np.savetxt('CT_results/times_nys_l2_reg_l2.csv', times_nys_l2_reg_l2, delimiter=',')
except:
    pass

In [ ]:
try:
    mse_nys_l2_reg_l1 = np.empty((nC,nb_iter))
    mse_train_nys_l2_reg_l1 = np.empty((nC,nb_iter))
    mae_nys_l2_reg_l1 = np.empty((nC,nb_iter))
    mae_train_nys_l2_reg_l1 = np.empty((nC,nb_iter))
    times_nys_l2_reg_l1 = np.empty((nC,nb_iter))

    for i,C in enumerate(tqdm(list_C)):
        for j in range(nb_iter):
            nys = Pipeline([('Scaler',StandardScaler()),
                            ('nys', SGDPlainNystromRegressor(m=1000, lambda_reg=C, penalty='l1')),])

            t0 = time()
            nys.fit(X_train, y_train)
            times_nys_l2_reg_l1[i,j] = time() - t0

            y_pred_train_nys = nys.predict(X_train)                      
            mse_train_nys_l2_reg_l1[i,j] = mean_squared_error(y_train, y_pred_train_nys)
            mae_train_nys_l2_reg_l1[i,j] = mean_absolute_error(y_train, y_pred_train_nys)

            y_pred_nys = nys.predict(X_test)                      
            mse_nys_l2_reg_l1[i,j] = mean_squared_error(y_test, y_pred_nys)
            mae_nys_l2_reg_l1[i,j] = mean_absolute_error(y_test, y_pred_nys)
except:
    pass

In [ ]:
try:
    np.savetxt('CT_results/mse_nys_l2_reg_l1.csv', mse_nys_l2_reg_l1, delimiter=',')
    np.savetxt('CT_results/mse_train_nys_l2_reg_l1.csv', mse_train_nys_l2_reg_l1, delimiter=',')
    np.savetxt('CT_results/mae_nys_l2_reg_l1.csv', mae_nys_l2_reg_l1, delimiter=',')
    np.savetxt('CT_results/mae_train_nys_l2_reg_l1.csv', mae_train_nys_l2_reg_l1, delimiter=',')
    np.savetxt('CT_results/times_nys_l2_reg_l1.csv', times_nys_l2_reg_l1, delimiter=',')
except:
    pass

In [ ]:
try:
    mse_nys_l1_reg_l1 = np.empty((nC,nb_iter))
    mse_train_nys_l1_reg_l1 = np.empty((nC,nb_iter))
    mae_nys_l1_reg_l1 = np.empty((nC,nb_iter))
    mae_train_nys_l1_reg_l1 = np.empty((nC,nb_iter))
    times_nys_l1_reg_l1 = np.empty((nC,nb_iter))

    for i,C in enumerate(tqdm(list_C)):
        for j in range(nb_iter):
            nys = Pipeline([('Scaler',StandardScaler()),
                            ('nys', SGDPlainNystromRegressor(m=1000, lambda_reg=C, penalty='l1', loss='epsilon_insensitive')),])

            t0 = time()
            nys.fit(X_train, y_train)
            times_nys_l1_reg_l1[i,j] = time() - t0

            y_pred_train_nys = nys.predict(X_train)                      
            mse_train_nys_l1_reg_l1[i,j] = mean_squared_error(y_train, y_pred_train_nys)
            mae_train_nys_l1_reg_l1[i,j] = mean_absolute_error(y_train, y_pred_train_nys)

            y_pred_nys = nys.predict(X_test)                      
            mse_nys_l1_reg_l1[i,j] = mean_squared_error(y_test, y_pred_nys)
            mae_nys_l1_reg_l1[i,j] = mean_absolute_error(y_test, y_pred_nys)
except:
    pass

In [ ]:
try:
    np.savetxt('CT_results/mse_nys_l1_reg_l1.csv', mse_nys_l1_reg_l1, delimiter=',')
    np.savetxt('CT_results/mse_train_nys_l1_reg_l1.csv', mse_train_nys_l1_reg_l1, delimiter=',')
    np.savetxt('CT_results/mae_nys_l1_reg_l1.csv', mae_nys_l1_reg_l1, delimiter=',')
    np.savetxt('CT_results/mae_train_nys_l1_reg_l1.csv', mae_train_nys_l1_reg_l1, delimiter=',')
    np.savetxt('CT_results/times_nys_l1_reg_l1.csv', times_nys_l1_reg_l1, delimiter=',')
except:
    pass

In [ ]:
try:
    mse_nys_l1_reg_l2 = np.empty((nC,nb_iter))
    mse_train_nys_l1_reg_l2 = np.empty((nC,nb_iter))
    mae_nys_l1_reg_l2 = np.empty((nC,nb_iter))
    mae_train_nys_l1_reg_l2 = np.empty((nC,nb_iter))
    times_nys_l1_reg_l2 = np.empty((nC,nb_iter))

    for i,C in enumerate(tqdm(list_C)):
        for j in range(nb_iter):
            nys = Pipeline([('Scaler',StandardScaler()),
                            ('nys', SGDPlainNystromRegressor(m=1000, lambda_reg=C, loss='epsilon_insensitive')),])

            t0 = time()
            nys.fit(X_train, y_train)
            times_nys_l1_reg_l2[i,j] = time() - t0

            y_pred_train_nys = nys.predict(X_train)                      
            mse_train_nys_l1_reg_l2[i,j] = mean_squared_error(y_train, y_pred_train_nys)
            mae_train_nys_l1_reg_l2[i,j] = mean_absolute_error(y_train, y_pred_train_nys)

            y_pred_nys = nys.predict(X_test)                      
            mse_nys_l1_reg_l2[i,j] = mean_squared_error(y_test, y_pred_nys)
            mae_nys_l1_reg_l2[i,j] = mean_absolute_error(y_test, y_pred_nys)
except:
    pass

In [ ]:
try:
    np.savetxt('CT_results/mse_nys_l1_reg_l2.csv', mse_nys_l1_reg_l2, delimiter=',')
    np.savetxt('CT_results/mse_train_nys_l1_reg_l2.csv', mse_train_nys_l1_reg_l2, delimiter=',')
    np.savetxt('CT_results/mae_nys_l1_reg_l2.csv', mae_nys_l1_reg_l2, delimiter=',')
    np.savetxt('CT_results/mae_train_nys_l1_reg_l2.csv', mae_train_nys_l1_reg_l2, delimiter=',')
    np.savetxt('CT_results/times_nys_l1_reg_l2.csv', times_nys_l1_reg_l2, delimiter=',')
except:
    pass

In [ ]:
try:
    mse_nys_l1 = np.empty((nD,nb_iter))
    mse_train_nys_l1 = np.empty((nD,nb_iter))
    mae_nys_l1 = np.empty((nD,nb_iter))
    mae_train_nys_l1 = np.empty((nD,nb_iter))
    times_nys_l1 = np.empty((nD,nb_iter))

    for i,D in enumerate(tqdm(list_D)):
        for j in range(nb_iter):
            nys = Pipeline([('Scaler',StandardScaler()),
                            ('nys', SGDPlainNystromRegressor(m=D, loss='epsilon_insensitive')),])

            t0 = time()
            nys.fit(X_train, y_train)
            times_nys_l1[i,j] = time() - t0

            y_pred_train_nys = nys.predict(X_train)                      
            mse_train_nys_l1[i,j] = mean_squared_error(y_train, y_pred_train_nys)
            mae_train_nys_l1[i,j] = mean_absolute_error(y_train, y_pred_train_nys)

            y_pred_nys = nys.predict(X_test)                      
            mse_nys_l1[i,j] = mean_squared_error(y_test, y_pred_nys)
            mae_nys_l1[i,j] = mean_absolute_error(y_test, y_pred_nys)
except:
    pass

In [ ]:
try:
    np.savetxt('CT_results/mse_nys_l1.csv', mse_nys_l1, delimiter=',')
    np.savetxt('CT_results/mse_train_nys_l1.csv', mse_train_nys_l1, delimiter=',')
    np.savetxt('CT_results/mae_nys_l1.csv', mae_nys_l1, delimiter=',')
    np.savetxt('CT_results/mae_train_nys_l1.csv', mae_train_nys_l1, delimiter=',')
    np.savetxt('CT_results/times_nys_l1.csv', times_nys_l1, delimiter=',')
except:
    pass

In [ ]:
try:
    mse_lin_l1_reg = np.empty((nC,1))
    mse_train_lin_l1_reg = np.empty((nC,1))
    mae_lin_l1_reg = np.empty((nC,1))
    mae_train_lin_l1_reg = np.empty((nC,1))
    times_lin_l1_reg = np.empty((nC,1))

    for i,D in enumerate(tqdm(list_C)):
        lin = Pipeline([('Scaler',StandardScaler()),
                        ('LinearSVR', LinearSVR(max_iter=10000, C=C)),])

        t0 = time()
        lin.fit(X_train, y_train)
        times_lin_l1_reg[i] = time() - t0

        y_pred_train_nys = lin.predict(X_train)                      
        mse_train_lin_l1_reg[i] = mean_squared_error(y_train, y_pred_train_nys)
        mae_train_lin_l1_reg[i] = mean_absolute_error(y_train, y_pred_train_nys)

        y_pred_nys = lin.predict(X_test)                      
        mse_lin_l1_reg[i] = mean_squared_error(y_test, y_pred_nys)
        mae_lin_l1_reg[i] = mean_absolute_error(y_test, y_pred_nys)
except:
    pass

In [ ]:
try:
    np.savetxt('CT_results/mse_lin_l1_reg.csv', mse_lin_l1_reg, delimiter=',')
    np.savetxt('CT_results/mse_train_lin_l1_reg.csv', mse_train_lin_l1_reg, delimiter=',')
    np.savetxt('CT_results/mae_lin_l1_reg.csv', mae_lin_l1_reg, delimiter=',')
    np.savetxt('CT_results/mae_train_lin_l1_reg.csv', mae_train_lin_l1_reg, delimiter=',')
    np.savetxt('CT_results/times_lin_l1_reg.csv', times_lin_l1_reg, delimiter=',')
except:
    pass

In [ ]:
try:
    mse_lin_l2_reg = np.empty((nC,1))
    mse_train_lin_l2_reg = np.empty((nC,1))
    mae_lin_l2_reg = np.empty((nC,1))
    mae_train_lin_l2_reg = np.empty((nC,1))
    times_lin_l2_reg = np.empty((nC,1))

    for i,C in enumerate(tqdm(list_C)):
        lin = Pipeline([('Scaler',StandardScaler()),
                        ('LinearSVR', LinearSVR(max_iter=10000, loss='squared_epsilon_insensitive', C=C)),])

        t0 = time()
        lin.fit(X_train, y_train)
        times_lin_l2_reg[i] = time() - t0

        y_pred_train_nys = lin.predict(X_train)                      
        mse_train_lin_l2_reg[i] = mean_squared_error(y_train, y_pred_train_nys)
        mae_train_lin_l2_reg[i] = mean_absolute_error(y_train, y_pred_train_nys)

        y_pred_nys = lin.predict(X_test)                      
        mse_lin_l2_reg[i] = mean_squared_error(y_test, y_pred_nys)
        mae_lin_l2_reg[i] = mean_absolute_error(y_test, y_pred_nys)
except:
    pass

In [ ]:
try:
    np.savetxt('CT_results/mse_lin_l2_reg.csv', mse_lin_l2_reg, delimiter=',')
    np.savetxt('CT_results/mse_train_lin_l2_reg.csv', mse_train_lin_l2_reg, delimiter=',')
    np.savetxt('CT_results/mae_lin_l2_reg.csv', mae_lin_l2_reg, delimiter=',')
    np.savetxt('CT_results/mae_train_lin_l2_reg.csv', mae_train_lin_l2_reg, delimiter=',')
    np.savetxt('CT_results/times_lin_l2_reg.csv', times_lin_l2_reg, delimiter=',')
except:
    pass

# Classification

In [ ]:
X, y = make_classification(n_samples=50000, n_features=120, n_informative=15, n_classes=2, random_state=17)
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=24)

In [ ]:
nC = 8
list_C = np.linspace(0.01,2,nC)
nb_iter = 10

In [ ]:
try:
    scores_lin_sh_l2 = np.empty((nC,1))
    scores_train_lin_sh_l2 = np.empty((nC,1))
    times_lin_sh_l2 = np.empty((nC,1))

    for i,C in enumerate(tqdm(list_C)):
        lin = Pipeline([('Scaler',StandardScaler()),
                        ('LinearSVC', LinearSVC(dual=False, C=C)),])

        t0 = time()
        lin.fit(X_train, y_train)
        times_lin_sh_l2[i] = time() - t0

        y_pred_train_lin = lin.predict(X_train)                      
        scores_train_lin_sh_l2[i] = accuracy_score(y_train, y_pred_train_lin)

        y_pred_lin = lin.predict(X_test)                      
        scores_lin_sh_l2[i] = accuracy_score(y_test, y_pred_lin)
except:
    pass

In [ ]:
try:
    np.savetxt('synthetic_clf_results/scores_lin_sh_l2.csv', scores_lin_sh_l2, delimiter=',')
    np.savetxt('synthetic_clf_results/scores_train_lin_sh_l2.csv', scores_train_lin_sh_l2, delimiter=',')
    np.savetxt('synthetic_clf_results/times_lin_sh_l2.csv', times_lin_sh_l2, delimiter=',')
except:
    pass

In [ ]:
try:
    scores_lin_sh_l1 = np.empty((nC,1))
    scores_train_lin_sh_l1 = np.empty((nC,1))
    times_lin_sh_l1 = np.empty((nC,1))

    for i,C in enumerate(tqdm(list_C)):
        lin = Pipeline([('Scaler',StandardScaler()),
                        ('LinearSVC', LinearSVC(dual=False, C=C, penalty='l1')),])

        t0 = time()
        lin.fit(X_train, y_train)
        times_lin_sh_l1[i] = time() - t0

        y_pred_train_lin = lin.predict(X_train)                      
        scores_train_lin_sh_l1[i] = accuracy_score(y_train, y_pred_train_lin)

        y_pred_lin = lin.predict(X_test)                      
        scores_lin_sh_l1[i] = accuracy_score(y_test, y_pred_lin)
except:
    pass

In [ ]:
try:
    np.savetxt('synthetic_clf_results/scores_lin_sh_l1.csv', scores_lin_sh_l1, delimiter=',')
    np.savetxt('synthetic_clf_results/scores_train_lin_sh_l1.csv', scores_train_lin_sh_l1, delimiter=',')
    np.savetxt('synthetic_clf_results/times_lin_sh_l1.csv', times_lin_sh_l1, delimiter=',')
except:
    pass

In [ ]:
try:
    scores_lin_h_l2 = np.empty((nC,1))
    scores_train_lin_h_l2 = np.empty((nC,1))
    times_lin_h_l2 = np.empty((nC,1))

    for i,C in enumerate(tqdm(list_C)):
        lin = Pipeline([('Scaler',StandardScaler()),
                        ('LinearSVC', LinearSVC(C=C, loss='hinge')),])

        t0 = time()
        lin.fit(X_train, y_train)
        times_lin_h_l2[i] = time() - t0

        y_pred_train_lin = lin.predict(X_train)                      
        scores_train_lin_h_l2[i] = accuracy_score(y_train, y_pred_train_lin)

        y_pred_lin = lin.predict(X_test)                      
        scores_lin_h_l2[i] = accuracy_score(y_test, y_pred_lin)
except:
    pass

In [ ]:
try:
    np.savetxt('synthetic_clf_results/scores_lin_h_l2.csv', scores_lin_h_l2, delimiter=',')
    np.savetxt('synthetic_clf_results/scores_train_lin_h_l2.csv', scores_train_lin_h_l2, delimiter=',')
    np.savetxt('synthetic_clf_results/times_lin_h_l2.csv', times_lin_h_l2, delimiter=',')
except:
    pass

In [ ]:
nD = 10
list_D = np.linspace(300,3500,nD,dtype=int)

In [ ]:
try:
    scores_rff_h_d = np.empty((nD,nb_iter))
    scores_train_rff_h_d = np.empty((nD,nb_iter))
    times_rff_h_d = np.empty((nD,nb_iter))

    for i,D in enumerate(tqdm(list_D)):
        for j in range(M):
            rff = Pipeline([('Scaler',StandardScaler()),
                            ('RFF',RFF(D = D)),
                            ('LinearSVC', LinearSVC(loss='hinge')),])

            t0 = time()
            rff.fit(X_train, y_train)
            times_rff_h_d[i,j] = time() - t0

            y_pred_train_rff = rff.predict(X_train)                      
            scores_train_rff_h_d[i,j] = accuracy_score(y_train, y_pred_train_rff)

            y_pred_rff = rff.predict(X_test)                      
            scores_rff_h_d[i,j] = accuracy_score(y_test, y_pred_rff)
except:
    pass

In [ ]:
try:
    np.savetxt('synthetic_clf_results/scores_rff_h_d.csv', scores_rff_h_d, delimiter=',')
    np.savetxt('synthetic_clf_results/scores_train_rff_h_d.csv', scores_train_rff_h_d, delimiter=',')
    np.savetxt('synthetic_clf_results/times_rff_h_d.csv', times_rff_h_d, delimiter=',')
except:
    pass